In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    certifi-2020.6.20          |   py36h9f0ad1d_0         151 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    geopy-2.0.0                |     pyh9f0ad1d_0          63 KB  conda-forge
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    ca-certificates-2020.6.20  |       hecda079_0         145 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0          conda-forge
    geopy:           

In [2]:
#Download New York Dataset
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [4]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [7]:
neighborhoods_data = newyork_data['features']

In [8]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [9]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [10]:
# fill the dataframe one row at a time.
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [11]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [12]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [13]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [14]:
#Define Foursquare Credentials and Version
CLIENT_ID = 'OLZ0JXV4LZDMG1ENPKIDSZKNGNBXISCSWQM02K32504N4242' # your Foursquare ID
CLIENT_SECRET = 'H05JCVG5TO4I1ARM3Q3ZA2AIOLTLCTKZKYRIVURHKDNCOIGN' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: OLZ0JXV4LZDMG1ENPKIDSZKNGNBXISCSWQM02K32504N4242
CLIENT_SECRET:H05JCVG5TO4I1ARM3Q3ZA2AIOLTLCTKZKYRIVURHKDNCOIGN


In [22]:
# Get the first neighborhood's name in the dataset.
neighborhoods.loc[0, 'Neighborhood']


'Wakefield'

In [23]:
# Get the first neighborhood's Borough in the dataset.
neighborhoods.loc[0, 'Borough']

'Bronx'

In [16]:
# Get the first neighborhood's Latitude and Longitude in the dataset.
neighborhood_latitude = neighborhoods.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = neighborhoods.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = neighborhoods.loc[0,  'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Wakefield are 40.89470517661, -73.84720052054902.


In [17]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=OLZ0JXV4LZDMG1ENPKIDSZKNGNBXISCSWQM02K32504N4242&client_secret=H05JCVG5TO4I1ARM3Q3ZA2AIOLTLCTKZKYRIVURHKDNCOIGN&v=20180605&ll=40.89470517661,-73.84720052054902&radius=500&limit=100'

In [18]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5f0338498a993d2972e0a718'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Wakefield',
  'headerFullLocation': 'Wakefield, Bronx',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 9,
  'suggestedBounds': {'ne': {'lat': 40.899205181110005,
    'lng': -73.84125857127495},
   'sw': {'lat': 40.89020517211, 'lng': -73.8531424698231}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4c537892fd2ea593cb077a28',
       'name': 'Lollipops Gelato',
       'location': {'address': '4120 Baychester Ave',
        'crossStreet': 'Edenwald & Bussing Ave',
        'lat': 40.894123150205274,
        'lng': -73.84589162362325,
        'labeledLatLn

In [27]:
#Explore Neighborhoods in New York City
# function that extracts the category of the venue
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [28]:
newyork_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker Heights
Gerritsen Beach
Marine Park
Clinton Hill
Sea Gate
Downtown
Boerum Hill
Prospect Lefferts Gardens
Ocean Hill
City Line
Bergen Beach
Midwood
Prospect Park South
Georgetown
East Williamsburg
North Side
South Side
Ocean Parkway
Fort Hamilton
Chinatown
Washington Heights
Inw

In [30]:
# size of resulting dataframe
print(newyork_venues.shape)
newyork_venues.head()

(10047, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1         Walgreens       40.896528       -73.844700        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3          Rite Aid       40.896649       -73.844846        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

In [31]:
#display how many venues were returned for each neighborhood
newyork_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      31                      31   
Annadale                                      13                      13   
Arden Heights                                  4                       4   
Arlington                                      5                       5   
Arrochar                                      21                      21   
Arverne                                       20                      20   
Astoria                                      100                     100   
Astoria Heights                               12                      12   
Auburndale                                    17                      17   
Bath Beach                                    43                      43   
Battery Park City                             63                      63   
Bay Ridge                                     81                      81   
Bay Terrace                                   48                      48   
Baychester                                    22                      22   
Bayside                                       80                      80   
Bayswater                                      1                       1   
Bedford Park                                  30                      30   
Bedford Stuyvesant                            30                      30   
Beechhurst                                    15                      15   
Bellaire                                      10                      10   
Belle Harbor                                  17                      17   
Bellerose                                     20                      20   
Belmont                                      100                     100   
Bensonhurst                                   26                      26   
Bergen Beach                                   6                       6   
Blissville                                    17                      17   
Bloomfield                                     4                       4   
Boerum Hill                                   87                      87   
Borough Park                                  22                      22   
Breezy Point                                   5                       5   
Briarwood                                      8                       8   
Brighton Beach                                44                      44   
Broad Channel                                  6                       6   
Broadway Junction                             17                      17   
Bronxdale                                     15                      15   
Brooklyn Heights                             100                     100   
Brookville                                     1                       1   
Brownsville                                   16                      16   
Bulls Head                                    46                      46   
Bushwick                                      73                      73   
Butler Manor                                   6                       6   
Cambria Heights                               11                      11   
Canarsie                                       7                       7   
Carnegie Hill                                 87                      87   
Carroll Gardens                              100                     100   
Castle Hill                                    5                       5   
Castleton Corners                             14                      14   
Central Harlem                                45                      45   
Charleston                                    29                      29   
Chelsea                                      106                     106   
Chinatown                                    100                     100   

In [32]:
#Display how many unique categories can be curated from all the returned venues
print('There are {} uniques categories.'.format(len(newyork_venues['Venue Category'].unique())))

There are 429 uniques categories.


In [33]:
#Analyze Each Neighborhood
# one hot encoding
newyork_onehot = pd.get_dummies(newyork_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
newyork_onehot['Neighborhood'] = newyork_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [newyork_onehot.columns[-1]] + list(newyork_onehot.columns[:-1])
newyork_onehot = newyork_onehot[fixed_columns]

newyork_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  Airport Terminal  American Restaurant  Antique Shop  \
0                   0                 0                    0             0   
1                   0                 0                    0             0   
2                   0                 0                    0             0   
3                   0                 0                    0             0   
4                   0                 0                    0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0              0                0          0           0           0       0   
1              0                0          0           0           0       0   
2              0                0          0           0           0       0   
3              0                0          0           0           0       0   
4              0                0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0     0    0               0                 0                 0   
1     0    0               0                 0                 0   
2     0    0               0                 0                 0   
3     0    0               0                 0                 0   
4     0    0               0                 0                 0   

   Basketball Stadium  Bath House  Beach  Beach Bar  Bed & Breakfast  \
0                   0           0      0          0                0   
1                   0           0      0          0                0   
2                   0           0      0          0                0   
3                   0           0      0          0                0   
4                   0           0      0          0                0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0         0            0           0              0                         0   
1         0            0           0              0                         0   
2         0            0           0              0                         0   
3         0            0           0              0                         0   
4       

In [34]:
# size of new dataframe size.
newyork_onehot.shape

(10047, 429)

In [35]:
#group rows by neighborhood and by taking the mean of the frequency of occurrence of each category
newyork_grouped = newyork_onehot.groupby('Neighborhood').mean().reset_index()
newyork_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                     Allerton     0.000000           0.000000   
1                     Annadale     0.000000           0.000000   
2                Arden Heights     0.000000           0.000000   
3                    Arlington     0.000000           0.000000   
4                     Arrochar     0.000000           0.000000   
5                      Arverne     0.000000           0.000000   
6                      Astoria     0.000000           0.000000   
7              Astoria Heights     0.000000           0.000000   
8                   Auburndale     0.000000           0.000000   
9                   Bath Beach     0.000000           0.000000   
10           Battery Park City     0.000000           0.000000   
11                   Bay Ridge     0.000000           0.000000   
12                 Bay Terrace     0.000000           0.020833   
13                  Baychester     0.000000           0.000000   
14                     Bayside     0.012500           0.000000   
15                   Bayswater     0.000000           0.000000   
16                Bedford Park     0.000000           0.000000   
17          Bedford Stuyvesant     0.000000           0.000000   
18                  Beechhurst     0.066667           0.000000   
19                    Bellaire     0.000000           0.000000   
20                Belle Harbor     0.000000           0.000000   
21                   Bellerose     0.000000           0.000000   
22                     Belmont     0.000000           0.000000   
23                 Bensonhurst     0.000000           0.000000   
24                Bergen Beach     0.000000           0.000000   
25                  Blissville     0.000000           0.000000   
26                  Bloomfield     0.000000           0.000000   
27                 Boerum Hill     0.022989           0.000000   
28                Borough Park     0.000000           0.000000   
29                Breezy Point     0.000000           0.000000   
30                   Briarwood     0.000000           0.000000   
31              Brighton Beach     0.000000           0.000000   
32               Broad Channel     0.000000           0.000000   
33           Broadway Junction     0.000000           0.000000   
34                   Bronxdale     0.000000           0.000000   
35            Brooklyn Heights     0.040000           0.000000   
36                  Brookville     0.000000           0.000000   
37                 Brownsville     0.000000           0.000000   
38                  Bulls Head     0.000000           0.000000   
39                    Bushwick     0.000000           0.000000   
40                Butler Manor     0.000000           0.000000   
41             Cambria Heights     0.000000           0.000000   
42                    Canarsie     0.000000           0.000000   
43               Carnegie Hill     0.034483           0.000000   
44             Carroll Gardens     0.000000           0.000000   
45                 Castle Hill     0.000000           0.000000   
46           Castleton Corners     0.000000           0.000000   
47              Central Harlem     0.000000           0.000000   
48                  Charleston     0.000000           0.000000   
49                     Chelsea     0.000000           0.000000   
50                   Chinatown     0.010000           0.000000   
51                 City Island     0.000000           0.000000   
52                   City Line     0.000000           0.000000   
53                Civic Center     0.030000           0.000000   
54           Claremont Village     0.000000           0.000000   
55                Clason Point     0.000000           0.000000   
56                     Clifton     0.000000           0.000000   
57                     Clinton     0.000000           0.000000   
58                Clinton Hill     0.032609           0.000000   
59                  Co-op City     0.000000           0.00

In [36]:
newyork_grouped.shape

(301, 429)

In [37]:
#print each neighborhood along with the top 5 most common venues
num_top_venues = 5

for hood in newyork_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = newyork_grouped[newyork_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
                venue  freq
0         Pizza Place  0.16
1         Supermarket  0.10
2       Deli / Bodega  0.06
3  Chinese Restaurant  0.06
4        Intersection  0.03


----Annadale----
                 venue  freq
0  American Restaurant  0.15
1          Pizza Place  0.15
2         Dance Studio  0.08
3         Liquor Store  0.08
4             Pharmacy  0.08


----Arden Heights----
               venue  freq
0           Pharmacy  0.25
1        Coffee Shop  0.25
2           Bus Stop  0.25
3        Pizza Place  0.25
4  Paella Restaurant  0.00


----Arlington----
                 venue  freq
0             Bus Stop   0.4
1        Deli / Bodega   0.2
2  American Restaurant   0.2
3        Boat or Ferry   0.2
4          Yoga Studio   0.0


----Arrochar----
                venue  freq
0            Bus Stop  0.14
1       Deli / Bodega  0.10
2  Italian Restaurant  0.10
3         Pizza Place  0.10
4        Liquor Store  0.05


----Arverne----
            venue  freq
0       Surf 

         venue  freq
0     Pharmacy   0.2
1         Bank   0.2
2        Diner   0.2
3       Market   0.2
4  Pizza Place   0.2


----Castleton Corners----
                 venue  freq
0          Pizza Place  0.21
1  Japanese Restaurant  0.07
2       Ice Cream Shop  0.07
3        Go Kart Track  0.07
4        Grocery Store  0.07


----Central Harlem----
                  venue  freq
0    Chinese Restaurant  0.07
1    African Restaurant  0.07
2   American Restaurant  0.04
3  Gym / Fitness Center  0.04
4                   Bar  0.04


----Charleston----
                    venue  freq
0           Big Box Store  0.07
1          Cosmetics Shop  0.07
2             Coffee Shop  0.07
3  Furniture / Home Store  0.03
4          Hardware Store  0.03


----Chelsea----
                 venue  freq
0          Coffee Shop  0.08
1          Art Gallery  0.07
2  American Restaurant  0.04
3       Ice Cream Shop  0.04
4   Italian Restaurant  0.04


----Chinatown----
                venue  freq
0  Chinese Res

                   venue  freq
0        Thai Restaurant  0.20
1     Mexican Restaurant  0.17
2     Chinese Restaurant  0.10
3        Bubble Tea Shop  0.07
4  Vietnamese Restaurant  0.07


----Eltingville----
              venue  freq
0       Pizza Place  0.14
1  Sushi Restaurant  0.11
2              Bank  0.06
3          Pharmacy  0.06
4    Sandwich Place  0.06


----Emerson Hill----
                        venue  freq
0  Construction & Landscaping  0.33
1                        Food  0.33
2               Moving Target  0.33
3                 Yoga Studio  0.00
4                Outlet Store  0.00


----Erasmus----
                  venue  freq
0  Caribbean Restaurant  0.17
1           Yoga Studio  0.04
2            Food Truck  0.04
3                School  0.04
4        Sandwich Place  0.04


----Far Rockaway----
                 venue  freq
0        Deli / Bodega  0.14
1   Chinese Restaurant  0.11
2          Pizza Place  0.11
3          Supermarket  0.07
4  Fried Chicken Joint  0.07




                venue  freq
0  Italian Restaurant  0.10
1          Bagel Shop  0.07
2            Pharmacy  0.07
3  Chinese Restaurant  0.05
4      Sandwich Place  0.05


----Howland Hook----
                 venue  freq
0   Italian Restaurant   1.0
1          Yoga Studio   0.0
2          Outlet Mall   0.0
3             Pet Café   0.0
4  Peruvian Restaurant   0.0


----Hudson Yards----
                  venue  freq
0                 Hotel  0.07
1    Italian Restaurant  0.05
2  Gym / Fitness Center  0.05
3                  Café  0.05
4           Coffee Shop  0.03


----Huguenot----
                venue  freq
0                Bank  0.22
1       Deli / Bodega  0.11
2  Italian Restaurant  0.11
3       Train Station  0.11
4          Donut Shop  0.11


----Hunters Point----
                 venue  freq
0                 Café  0.06
1   Italian Restaurant  0.06
2  Japanese Restaurant  0.04
3       Scenic Lookout  0.03
4         Burger Joint  0.03


----Hunts Point----
            venue  freq
0

              venue  freq
0       Pizza Place  0.42
1          Pharmacy  0.08
2            Market  0.08
3    Ice Cream Shop  0.08
4  Video Game Store  0.08


----Mill Basin----
                 venue  freq
0   Chinese Restaurant  0.11
1  Japanese Restaurant  0.09
2          Pizza Place  0.09
3     Sushi Restaurant  0.06
4                 Bank  0.06


----Mill Island----
          venue  freq
0     Locksmith   0.5
1          Pool   0.5
2   Yoga Studio   0.0
3  Outlet Store   0.0
4      Pet Café   0.0


----Morningside Heights----
                 venue  freq
0  American Restaurant  0.07
1          Coffee Shop  0.07
2            Bookstore  0.07
3                 Park  0.07
4         Burger Joint  0.05


----Morris Heights----
                venue  freq
0       Grocery Store  0.12
1  Spanish Restaurant  0.12
2       Deli / Bodega  0.12
3         Pizza Place  0.12
4            Pharmacy  0.12


----Morris Park----
           venue  freq
0    Pizza Place  0.15
1   Burger Joint  0.08
2  Deli

                venue  freq
0               Hotel  0.20
1      Sandwich Place  0.13
2          Hotel Pool  0.07
3  Spanish Restaurant  0.07
4  Athletics & Sports  0.07


----Randall Manor----
           venue  freq
0  Deli / Bodega   0.2
1       Bus Stop   0.2
2   Home Service   0.2
3           Park   0.2
4     Playground   0.2


----Ravenswood----
                 venue  freq
0  Japanese Restaurant  0.04
1               Market  0.04
2  Fried Chicken Joint  0.04
3                Diner  0.04
4           Food Truck  0.04


----Red Hook----
                 venue  freq
0          Art Gallery  0.08
1   Seafood Restaurant  0.08
2                 Park  0.06
3  American Restaurant  0.06
4                  Bar  0.06


----Rego Park----
            venue  freq
0          Bakery  0.11
1   Grocery Store  0.05
2        Pharmacy  0.05
3  Sandwich Place  0.05
4     Pizza Place  0.05


----Remsen Village----
                  venue  freq
0  Caribbean Restaurant  0.19
1  Fast Food Restaurant  0.12
2  

                 venue  freq
0                Trail   0.5
1                 Park   0.5
2          Yoga Studio   0.0
3          Outlet Mall   0.0
4  Peruvian Restaurant   0.0


----Tompkinsville----
                venue  freq
0       Deli / Bodega  0.12
1         Pizza Place  0.12
2             Brewery  0.08
3  Mexican Restaurant  0.04
4                Park  0.04


----Tottenville----
                    venue  freq
0           Deli / Bodega  0.17
1      Mexican Restaurant  0.17
2      Italian Restaurant  0.17
3  Thrift / Vintage Store  0.17
4          Cosmetics Shop  0.17


----Travis----
           venue  freq
0          Hotel  0.21
1  Bowling Alley  0.14
2            Gym  0.14
3  Deli / Bodega  0.07
4    Sports Club  0.07


----Tribeca----
                 venue  freq
0  American Restaurant  0.06
1                 Park  0.06
2   Italian Restaurant  0.06
3                 Café  0.04
4     Greek Restaurant  0.04


----Tudor City----
                venue  freq
0                Park  0

In [38]:
#function to sort the venues in descending order.
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [40]:
#Create the new dataframe and display the top 10 venues for each neighborhood.
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = newyork_grouped['Neighborhood']

for ind in np.arange(newyork_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(newyork_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place           Supermarket   
1       Annadale           Pizza Place   American Restaurant   
2  Arden Heights              Pharmacy           Coffee Shop   
3      Arlington              Bus Stop         Deli / Bodega   
4       Arrochar              Bus Stop    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue     5th Most Common Venue  \
0         Deli / Bodega    Chinese Restaurant              Intersection   
1            Restaurant              Pharmacy              Dance Studio   
2              Bus Stop           Pizza Place             Women's Store   
3   American Restaurant         Boat or Ferry             Women's Store   
4         Deli / Bodega           Pizza Place  Mediterranean Restaurant   

  6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
0                   Spa         Grocery Store  Check Cashing Service   
1        Cosmetics Shop            Sports Bar                   Food   
2                 Field           Event Space                Exhibit   
3           Fish Market            Eye Doctor                Factory   
4            Food Truck            Bagel Shop           Liquor Store   

  9th Most Common Venue 10th Most Common Venue  
0     Martial Arts Dojo   Fast Food Restaurant  
1         Train Station           Liquor Store  
2            Eye Doctor                Factory  
3    Falafel Restaurant                   Farm  
4        Sandwich Place     Athletics & Sports

In [47]:
#Cluster Neighborhoods
# set number of clusters
kclusters = 5

newyork_grouped_clustering = newyork_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(newyork_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 1, 1, 3, 3, 0, 3, 3], dtype=int32)

In [50]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

newyork_merged = neighborhoods

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
newyork_merged = newyork_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

newyork_merged.head() # check the last columns!

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201             0.0   
1   Bronx   Co-op City  40.874294 -73.829939             0.0   
2   Bronx  Eastchester  40.887556 -73.827806             0.0   
3   Bronx    Fieldston  40.895437 -73.905643             3.0   
4   Bronx    Riverdale  40.890834 -73.912585             3.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Pharmacy        Ice Cream Shop        Sandwich Place   
1           Bus Station   Fried Chicken Joint        Discount Store   
2  Caribbean Restaurant         Deli / Bodega                 Diner   
3                 Plaza                 River           Bus Station   
4                  Park           Bus Station                  Bank   

        4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0                  Donut Shop           Gas Station          Dessert Shop   
1              Baseball Field         Grocery Store            Bagel Shop   
2                 Bus Station              Bus Stop    Seafood Restaurant   
3  Financial or Legal Service         Event Service           Event Space   
4                  Food Truck                   Gym                 Plaza   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0            Laundromat                  Food           Flea Market   
1          Liquor Store              Pharmacy  Fast Food Restaurant   
2         Bowling Alley         Metro Station  Fast Food Restaurant   
3               Exhibit            Eye Doctor               Factory   
4          Home Service  Fast Food Restaurant           Event Space   

  10th Most Common Venue  
0         Farmers Market  
1            Pizza Place  
2        Automotive Shop  
3     Falafel Restaurant  
4                Exhibit

In [83]:
#newyork_merged['Cluster Labels'] =newyork_merged['Cluster Labels'].astype(int)

In [82]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(newyork_merged['Latitude'], newyork_merged['Longitude'],newyork_merged['Neighborhood'], newyork_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
       #color=rainbow[cluster -1],
        fill=True,
       # fill_color=rainbow[cluster -1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Exam
## Cluster 1

In [71]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 0, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood      1st Most Common Venue  \
0               Wakefield                   Pharmacy   
1              Co-op City                Bus Station   
2             Eastchester       Caribbean Restaurant   
5             Kingsbridge                Pizza Place   
7                Woodlawn              Deli / Bodega   
8                 Norwood                Pizza Place   
10             Baychester                       Bank   
11         Pelham Parkway                Pizza Place   
13           Bedford Park                      Diner   
14     University Heights                Pizza Place   
15         Morris Heights                Pizza Place   
16                Fordham          Mobile Phone Shop   
17           East Tremont                Pizza Place   
19           High  Bridge         Chinese Restaurant   
20                Melrose                Pizza Place   
21             Mott Haven                        Gym   
23               Longwood  Latin American Restaurant   
24            Hunts Point             Farmers Market   
25             Morrisania                Bus Station   
26              Soundview         Chinese Restaurant   
30            Parkchester                Supermarket   
31     Westchester Square       Fast Food Restaurant   
33            Morris Park                Pizza Place   
34                Belmont         Italian Restaurant   
36        North Riverdale                Pizza Place   
38          Schuylerville                   Pharmacy   
40            Castle Hill                       Bank   
42         Pelham Gardens                   Pharmacy   
43              Concourse              Grocery Store   
44              Unionport                      Diner   
45               Edenwald                 Playground   
47            Bensonhurst         Chinese Restaurant   
48            Sunset Park                     Bakery   
50              Gravesend              Deli / Bodega   
53      Manhattan Terrace                Pizza Place   
54               Flatbush              Deli / Bodega   
55          Crown Heights                Pizza Place   
71          Cypress Hills                 Donut Shop   
72          East New York       Fast Food Restaurant   
73          Starrett City                Bus Station   
80           Borough Park                       Bank   
82        Gerritsen Beach                Pizza Place   
83            Marine Park             Baseball Field   
89             Ocean Hill              Deli / Bodega   
90              City Line                 Donut Shop   
92                Midwood                Pizza Place   
93    Prospect Park South       Caribbean Restaurant   
94             Georgetown                       Bank   
98          Ocean Parkway           Sushi Restaurant   
99          Fort Hamilton                Pizza Place   
103      Hamilton Heights                Pizza Place   
137         Richmond Hill  Latin American Restaurant   
140             Sunnyside                Pizza Place   
142               Maspeth                Pizza Place   
144              Glendale                    Brewery   
145             Rego Park                     Bakery   
146             Woodhaven              Deli / Bodega   
147            Ozone Park                   Pharmacy   
149         College Point              Deli / Bodega   
154            Douglaston                       Bank   
155             Glen Oaks                   Pharmacy   
156             Bellerose                Pizza Place   
157     Kew Gardens Hills                       Bank   
158         Fresh Meadows                Bus Station   
161       Oakland Gardens          Korean Restaurant   
164         South Jamaica                Bus Station   
169              Rosedale             Baseball Field   
170          Far Rockaway              Deli / Bodega   
171         Broad Channel        Sporting Goods Shop   
174            Beechhurst         Chinese Restaurant   
181           Floral Park          In

## Cluster 2

In [58]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 1, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue  2nd Most Common Venue  \
28        Throgs Neck                   Bar             Sports Bar   
32           Van Nest         Deli / Bodega            Pizza Place   
39     Edgewater Park    Italian Restaurant          Deli / Bodega   
150        Whitestone          Dance Studio        Bubble Tea Shop   
159         Briarwood         Deli / Bodega             Playground   
198      New Brighton              Bus Stop                   Park   
202       Grymes Hill         Deli / Bodega                Dog Run   
204       South Beach         Deli / Bodega                  Beach   
206  Mariner's Harbor    Italian Restaurant          Deli / Bodega   
217       Tottenville    Italian Restaurant         Cosmetics Shop   
227         Arlington              Bus Stop          Deli / Bodega   
228          Arrochar              Bus Stop     Italian Restaurant   
234    New Dorp Beach    Italian Restaurant          Deli / Bodega   
252       Shore Acres    Italian Restaurant               Bus Stop   
254           Concord   Peruvian Restaurant     Athletics & Sports   
256     Randall Manor            Playground          Deli / Bodega   
257      Howland Hook    Italian Restaurant  Entertainment Service   
258          Elm Park         Deli / Bodega               Bus Stop   
296           Madison         Deli / Bodega             Bagel Shop   

         3rd Most Common Venue       4th Most Common Venue  \
28            Asian Restaurant                 Coffee Shop   
32   Middle Eastern Restaurant                  Hookah Bar   
39                 Pizza Place                  Donut Shop   
150              Deli / Bodega                 Candy Store   
159        Arts & Crafts Store                         Gym   
198              Deli / Bodega              Discount Store   
202              Women's Store  Financial or Legal Service   
204                       Pier          Athletics & Sports   
206                   Bus Stop          Athletics & Sports   
217     Thrift / Vintage Store               Deli / Bodega   
227        American Restaurant               Boat or Ferry   
228              Deli / Bodega                 Pizza Place   
234                       Food           Other Repair Shop   
252                        Bar                Intersection   
254         Italian Restaurant      Thrift / Vintage Store   
256                       Park                    Bus Stop   
257              Event Service                 Event Space   
258         Italian Restaurant         American Restaurant   
296         Italian Restaurant                  Restaurant   

        5th Most Common Venue       6th Most Common Venue  \
28        American Restaurant                 Pizza Place   
32                  BBQ Joint                  Donut Shop   
39                        Pub                  Sports Bar   
150             Women's Store  Financial or Legal Service   
159               Bus Station                 Coffee Shop   
198             Bowling Alley                  Playground   
202               Event Space                     Exhibit   
204             Women's Store         Filipino Restaurant   
206               Supermarket               Women's Store   
217                  Bus Stop          Mexican Restaurant   
227             Women's Store                 Fish Market   
228  Mediterranean Restaurant                  Food Truck   
234            Scenic Lookout                  Sports Bar   
252             Deli / Bodega                Dance Studio   
254             Deli / Bodega        Gym / Fitness Center   
256              Home Service               Women's Store   
257                   Exhibit                  Eye Doctor   
258                Toll Plaza                 Pizza Place   
296               Pizza Place                         Spa   

          7th Most Common Venue       8th Most Common Venue  \
28                Deli / Bodega          Italian Restaurant   
32               Sho

## Cluster 3

In [59]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 2, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue      2nd Most Common Venue  \
27   Clason Point                  Park  South American Restaurant   
192    Somerville                  Park              Women's Store   
203     Todt Hill                 Trail                       Park   
225   Westerleigh     Convenience Store                       Park   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
27       Convenience Store         Grocery Store              Bus Stop   
192  Entertainment Service         Event Service           Event Space   
203          Women's Store                 Field         Event Service   
225                 Arcade        Baseball Field         Women's Store   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
27                   Pool         Boat or Ferry   Filipino Restaurant   
192               Exhibit            Eye Doctor               Factory   
203           Event Space               Exhibit            Eye Doctor   
225   Filipino Restaurant           Event Space               Exhibit   

    9th Most Common Venue 10th Most Common Venue  
27                Exhibit             Eye Doctor  
192    Falafel Restaurant                   Farm  
203               Factory     Falafel Restaurant  
225            Eye Doctor                Factory

## Cluster 4

In [60]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 3, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood        1st Most Common Venue  \
3                    Fieldston                        Plaza   
4                    Riverdale                         Park   
6                  Marble Hill               Sandwich Place   
9               Williamsbridge                    Nightclub   
12                 City Island           Seafood Restaurant   
18                  West Farms                  Bus Station   
22                 Port Morris       Furniture / Home Store   
29                Country Club               Sandwich Place   
35              Spuyten Duyvil                         Park   
37                  Pelham Bay                         Bank   
41                   Olinville         Caribbean Restaurant   
46                   Bay Ridge                          Spa   
49                  Greenpoint                          Bar   
51              Brighton Beach  Eastern European Restaurant   
52              Sheepshead Bay                 Dessert Shop   
56               East Flatbush           Chinese Restaurant   
57                  Kensington                Grocery Store   
58             Windsor Terrace                         Café   
59            Prospect Heights                          Bar   
60                 Brownsville           Chinese Restaurant   
61                Williamsburg                  Coffee Shop   
62                    Bushwick                          Bar   
63          Bedford Stuyvesant                  Coffee Shop   
64            Brooklyn Heights                  Yoga Studio   
65                 Cobble Hill                  Pizza Place   
66             Carroll Gardens           Italian Restaurant   
67                    Red Hook           Seafood Restaurant   
68                     Gowanus       Furniture / Home Store   
69                 Fort Greene           Italian Restaurant   
70                  Park Slope                  Coffee Shop   
74                    Canarsie             Asian Restaurant   
75                   Flatlands                     Pharmacy   
76                 Mill Island                    Locksmith   
77             Manhattan Beach                     Bus Stop   
78                Coney Island             Baseball Stadium   
79                  Bath Beach                     Pharmacy   
81               Dyker Heights                  Golf Course   
84                Clinton Hill                  Pizza Place   
85                    Sea Gate                  Sports Club   
86                    Downtown                  Pizza Place   
87                 Boerum Hill                 Dance Studio   
88   Prospect Lefferts Gardens                       Bakery   
91                Bergen Beach              Harbor / Marina   
95           East Williamsburg                          Bar   
96                  North Side                  Coffee Shop   
97                  South Side                          Bar   
100                  Chinatown           Chinese Restaurant   
101         Washington Heights                         Café   
102                     Inwood                       Lounge   
104             Manhattanville                  Coffee Shop   
105             Central Harlem           Chinese Restaurant   
106                East Harlem           Mexican Restaurant   
107            Upper East Side           Italian Restaurant   
108                  Yorkville           Italian Restaurant   
109                 Lenox Hill                  Coffee Shop   
110           Roosevelt Island                         Park   
111            Upper West Side           Italian Restaurant   
112             Lincoln Square         Gym / Fitness Center   
113                    Clinton                      Theater   
114                    Midtown                  Coffee Shop   
115                Murray Hill            Korean Restaurant   
116                    Chelsea                  Coffee Shop   
117          Greenwich Village           Italian 

## Cluster 5

In [61]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 4, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
193   Brookville         Deli / Bodega         Women's Store   

          3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
193  Financial or Legal Service         Event Service           Event Space   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
193               Exhibit            Eye Doctor               Factory   

    9th Most Common Venue 10th Most Common Venue  
193    Falafel Restaurant                   Farm

In [66]:
neighborhoods.loc[193,'Neighborhood']

'Brookville'

In [68]:
potential_latitude = neighborhoods.loc[193, 'Latitude'] # neighborhood latitude value
potential_longitude = neighborhoods.loc[193, 'Longitude'] # neighborhood longitude value

potential_name = neighborhoods.loc[193, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(potential_name, 
                                                               potential_latitude, 
                                                               potential_longitude))

Latitude and longitude values of Brookville are 40.66000322733613, -73.75175310731153.


## Conclusion

The Fifth Cluster identified through my analysis designates Brookville as a potential area to look for space for the potential restaurant venue due to multiple event spaces in the area and limited competition in the area as demonstrated by only having 2 out of ten common venues being food. Of those two common venues they are either falafel restaurants or deli/bodegas. There is also the increased revenue opportunities of partnering with the event and exhibit spaces for catering of events. Finally the proximity to farms which is listed as the 10th most common venue allows for an increased potential savings on food while also being able to advertise as local farm to table restaurant in New York City.
